# Space-time partial differential equation: Study of the diffusive equation (implicit methods)

In [1]:
import numpy as np
import matplotlib.pyplot as plt
plt.style.use('seaborn-v0_8-whitegrid')
import matplotlib as mpl
mpl.rc('lines', linewidth=2)

from nm_lib import nm_lib as nm

Let's consider now the viscous term in Burger's equation: 

$$\frac{\partial u}{\partial t} = \nu \frac{\partial^2 u}{\partial x^2}, \tag{1}$$

## 1- Apply an explicit method. 

What would be the CFL condition for a viscous term where $\nu$ is either a constant or an array that depends on $x$. 

> XXX PUT MATH HERE

We would like to solve equation (1) numerically for $x  [x_0, x_f]$ with $x_0 = −2.6$, $x_f = 2.6$, periodic boundary conditions and with the initial condition:

$$u(x,t=t_0) = A\exp(-(x-x_0)^2/W^2)   \tag{2}$$

with $A=0.3$, $W=0.1$, and $x_0=0$. __Suggestion__: Apply the first derivative upwind and the second downwind. Apply Von Newman analysis. Is it stable? What is the time-step dependence with $\Delta x$? 

How many steps are needed to reach a $t=1.8$ for $nump=128$? And $256$? 

In [2]:
def u_0(x, A=0.3, W=0.1, x0=0):
    r"""Initial condition for the burger equation."""
    return A * np.exp( -(x - x0)**2 / W**2 )

x0 = -2.6
xf = 2.6

nx = 128
nt = 200
xx = np.linspace(x0, xf, nx) 
a=0.1
t, unnt_Lax = nm.evolve(xx, u_0(xx), a=a, nt=nt, cfl_cut=0.98, bnd_limits=[1, 0])


TypeError: cfl_diff_burger() got multiple values for argument 'a'

In [12]:
# Setup for animations
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def init(): 
    """Initialize animation"""
    axes.plot(xx,unnt_Lax[:,0], label='Lax')
    axes.legend(loc='upper right')

def animate(i):
    """Animate the solution with dynamic axis limits"""
    axes.clear()
    axes.plot(xx,unnt_Lax[:,i], label='Lax') 
    axes.set_title('t=%.2f'%t[i])
    axes.legend(loc='upper right')

fig, axes = plt.subplots(figsize=(7, 3))
anim = FuncAnimation(fig, animate, interval=20, frames=nt, init_func=init)
plt.close(); HTML(anim.to_jshtml())

> XXXXXXXXXX Look at this one closer.


<span style="color:pink"> JMS. </span>.

<span style="color:red"> This is not evolv_Lax_uadv_burgers function, use evolv which is almost ready where
you compute first one time upwind derivative and then one time downwind. This will do it. Note that you need to use here cfl_diff but this is wrongly calculated too. </span>.

## Choose one of the following options: 

## 2- Implicit methods.

In the [wiki](https://github.com/AST-Course/AST5110/wiki/Implicit-methods), we describe some implicit or semi-explicit methods that allow relaxing the CFL constraint on diffusive terms. Consider Newton-Rapson method and repeat the previous numerical experiment. For this, you will need to implement the following   


$F_j = u^{n+1}_j - u^n_j - \nu \, (u^{n+1}_{j+1} - 2u^{n+1}_{j}+u^{n+1}_{j-1})\frac{\Delta t}{\Delta x^2}$

in `NR_f` and `step_diff_burgers` functions in `nm_lib`. 

And the Jacobian can be easily built. 

$J(j,k) = F_j'(u^{n+1}_k)$

fill in the `jacobian` function in `nm_lib`. Note that this matrix is linear with $u$. 

Test the model with [wiki](https://github.com/AST-Course/AST5110/wiki/Self-similar-solution-for-parabolic-eq) self-similar solutions. How long it takes each time step compared to the Lax-method? Use `time.time` library. Do it for nump=256, nt=30 and dt = 0.1. In order to test the simulation, use `curve_fit` from `scipy.optimize`. 

__hint__ consider to use a good initial guess (`p0`) in and `bnd_limits` to facilitate the fitting wiht `curve_fit`. What happens to the solution when increasing dt? How much can be improved in limiting the tolerance?

In [6]:
a = 1
dt = 0.3

t, unnt, errt, countt = nm.Newton_Raphson(xx, u_0(xx), a, dt, nt)

In [7]:
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

def init(): 
    """Initialize animation"""
    axes.plot(xx,unnt[:,0])

def animate(i):
    """Animate the solution with dynamic axis limits"""
    axes.clear()
    axes.plot(xx,unnt[:,i]) 
    axes.set_title('t=%.2f'%t[i])

fig, axes = plt.subplots(figsize=(7, 3))
anim = FuncAnimation(fig, animate, interval=20, frames=nt, init_func=init)
plt.close(); HTML(anim.to_jshtml())

<span style="color:pink"> JMS. </span>.

<span style="color:red"> Change the output of NR_f to (with dx**2): 

    F_j =  un - uo - a * (np.roll(un, -1) - 2 * un + np.roll(un, 1)) * dt / dx**2
    


----------------------------------------------

Let's consider a non-linear function where $\nu$ depends on $u$. To keep it simple, solve the following: 

$\frac{\partial u}{\partial t} = u \frac{\partial^2 u}{\partial x^2}$

where $\nu_0$ is a constant and the same initial conditions as the previous exercise (fill in `Newton_Raphson_u`, `jacobian_u` and `NR_f_u`. Consider an error limit of $10^{-4}$ and compare the previous exercise (with the same error limit). How many iterations needs now the method to converge to the right solution? Why? Increase `ncount` to 1000. 

## 3- Semi-explicit methods. 

__a)__ Super-time-stepping (STS) schemes work for parabolic terms. STS is an API method that performs a subset of "unstable" intermediate steps, but the sum of all the steps is stable. Visualize how `taui_sts` varies with $nu$ and $niter$. Compare the solution with the analytical one for the final and intermediate STS steps. For the full STS steps, how improves the solution with $nu$? and $niter$? Is there a relation between the error and these two parameters, $nu$, and $niter$? For which $niter$ and $nu$ the method provides larger steps than an ordinary explicit. For this exercise, fill in `evol_sts`, and `taui_sts`. 